In [1]:
import pandas as pd
import os

In [5]:
dataset_path = "../../data/translated/en/ucberkeley-dlab_measuring-hate-speech_translated_positive_en_translated.csv"

df = pd.read_csv(dataset_path, index_col=[0])
df

comment_id  annotator_id  platform  sentiment  respect  insult  \
0            47777         10873         3        0.0      0.0     0.0   
1            39773          2790         2        0.0      0.0     0.0   
2            47101          3379         3        4.0      4.0     4.0   
3            43625          7365         3        2.0      3.0     2.0   
4            12538           488         0        4.0      4.0     4.0   
...            ...           ...       ...        ...      ...     ...   
135551       37080          8590         2        1.0      1.0     0.0   
135552       22986          8303         2        2.0      0.0     0.0   
135553       21008          6207         2        1.0      1.0     1.0   
135554       22986          7886         2        2.0      0.0     0.0   
135555       14785          6897         0        4.0      4.0     4.0   

        humiliate  status  dehumanize  violence  ...  \
0             0.0     2.0         0.0       0.0  ...   
1             0.0     2.0         0.0       0.0  ...   
2             4.0     4.0         4.0       0.0  ...   
3             1.0     2.0         0.0       0.0  ...   
4             4.0     4.0         4.0       4.0  ...   
...           ...     ...         ...       ...  ...   
135551        0.0     2.0         0.0       0.0  ...   
135552        0.0     2.0         0.0       0.0  ...   
135553        1.0     1.0         0.0       0.0  ...   
135554        0.0     2.0         0.0       0.0  ...   
135555        2.0     2.0         2.0       3.0  ...   

        annotator_religion_jewish  annotator_religion_mormon  \
0                           False                      False   
1                           False                      False   
2                           False                      False   
3                           False                      False   
4                           False                      False   
...                           ...                        ...   
135551                      False                      False   
135552                      False                      False   
135553                      False                      False   
135554                      False                      False   
135555                      False                      False   

        annotator_religion_muslim  annotator_religion_nothing  \
0                           False                       False   
1                           False                       False   
2                           False                        True   
3                           False                       False   
4                           False                       False   
...                           ...                         ...   
135551                      False                       False   
135552                      False                       False   
135553                      False                       False   
135554                      False                        True   
135555                      False                       False   

       annotator_religion_other  annotator_sexuality_bisexual  \
0                         False                         False   
1                         False                         False   
2                         False                         False   
3                         False                         False   
4                         False                         False   
...                         ...                           ...   
135551                    False                         False   
135552                     True                          True   
135553                    False                         False   
135554                    False                         False   
135555                    False                         False   

        annotator_sexuality_gay  annotator_sexuality_straight  \
0                         False                   

In [6]:
# Preprocessing
import os
import re

def clean_text(text):
    
    patterns = ["(", ")", "Name", "URL", "NAME", "probably does not need a translation", "(optional", "optional,"]
    out = text
    for p in patterns:
        out = out.replace(p, "")
        
    #out = "".join([x for x in out if x.isascii() or x == " "])
    
    out = re.sub("#[0-9]", "", out)
    out = re.sub(r"& 60;", "", out)
    out = out.replace("#", "") # supression des hashtag après erreur de decoding
    out = out.replace("@", "")
    
    return out

OUTPUT_DIR = "../data/processed/"
if not os.path.exists(OUTPUT_DIR):
    os.makedirs(OUTPUT_DIR)

worst_threshold = 0.9
best_threshold = 0.1

avg_score = pd.DataFrame(df.groupby("translated").hate_speech_score.mean())
avg_score = avg_score.sort_values("hate_speech_score", ascending=False).reset_index()
avg_score["translated_clean"] = avg_score.translated.apply(clean_text)

worst_df = avg_score.loc[avg_score.hate_speech_score > 0]
n_worst = worst_df.shape[0]

best_df = avg_score.loc[avg_score.hate_speech_score < 0]
best_df = best_df.iloc[:n_worst] # keep balancing

worst_df["label"] = 1
best_df["label"] = 0

print("Worst :", worst_df.shape[0])
print("Best :", best_df.shape[0])

worst_df.to_csv(os.path.join(OUTPUT_DIR, "uc-berkeley-measuring-hate-speech-positive-translated.csv"))
best_df.to_csv(os.path.join(OUTPUT_DIR, "uc-berkeley-measuring-hate-speech-negative-translated.csv"))

Worst : 14206
Best : 14206


/tmp/ipykernel_18064/1870029499.py:38: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  worst_df["label"] = 1
